# Amide-aromatic interaction analysis using PDB and BMRB archives
## Introduction
The objective of the notebook is to understand the anomalous chemical shifts of amide protons as a result of hydrogen bond interaction between the amide proton  and the near by aromatic side-chain. For this study we are going to use the chemical shift information available in BMRB database (https://bmrb.io) and the geometric information available in wwPDB(http://www.wwpdb.org). 

### Quick overview of the steps

* Find the matching BMRB and PDB Ids. This information is available via BMRB-API(http://api.bmrb.io/v2/mappings/bmrb/pdb?match_type=exact) and as well as BMRB-FTP (https://bmrb.io/ftp/pub/bmrb/nmr_pdb_integrated_data/adit_nmr_matched_pdb_bmrb_entry_ids.csv)
* Extract the amide chemical shifts from the NMR-STAR file and calculate the Z-score
* Extract the coordinate information from CIF file and calculate the distance between the amide proton and the center of the nearest aromatic ring, azimuthal angle and solid angle for each amide proton. 
* Combine the information from NMR-STAR(BMRB) and CIF(wwPDB) using atom identifier(seq_id,chain_id,residue,atom)
* write the output as csv file
* repeat the step for all matching PDB and BMRB ids. 

## Import the necessary python packages 
Please make sure you have installed all the necessary packages(pynmrstar,mmcif and numpy). For plotting you may need plotly and csv

In [12]:
import pynmrstar
from mmcif.io.PdbxReader import PdbxReader
import os
import numpy
import csv
import gzip
import plotly.express as px
from typing import Union, List, Optional

##  Extract chemical shift information and calculate the Z-score

We are going to use the pynmrstr (https://pypi.org/project/pynmrstar/) package to parse the NMR-STAR file. The Z-score is calculated using mean and the standard deviation from the BMRB statistics (https://bmrb.io/ref_info/stats.php?restype=aa&set=filt)
Let us first write a function to calculate the Z-score
### Function to calculate Z-score

In [8]:
def get_z_score(res: str, amide_cs: float) -> float:
    """
    Calculates Z-score for a given amide chemical shift
    :param res: residue name
    :param amide_cs: chemical shift
    :return: Z-score
    """
    m = {'ALA':8.194,'ARG':8.234,'ASN':8.324,'ASP':8.300,'CYS':8.386,'GLN':8.219,'GLU':8.330,'GLY':8.330,
         'HIS':8.247,'ILE':8.262,'LEU':8.215,'LYS':8.177,'MET':8.251,'PHE':8.335,'SER':8.277,'THR':8.232,
         'TRP':8.264,'TYR':8.289,'VAL':8.270}
    sd = {'ALA':0.577,'ARG':0.601,'ASN':0.610,'ASP':0.558,'CYS':0.670,'GLN':0.569,'GLU':0.576,'GLY':0.619,
         'HIS':0.666,'ILE':0.674,'LEU':0.627,'LYS':0.589,'MET':0.575,'PHE':0.710,'SER':0.568,'THR':0.610,
         'TRP':0.761,'TYR':0.721,'VAL':0.659}
    try:
        z_score = (amide_cs - m[res]) / sd[res]
    except KeyError:
        z_score = 0.00
    return round(z_score,3)

The above function will calculate the Z-score for a given amide proton chemical shift and residue type. For example

In [9]:
get_z_score('LEU',5.33)

-4.601

## Function to parse the chemical shift and calculate the Z-score
First let us define aromatic residues and their atoms. 

In [10]:
aromatic_atoms = {
    'PHE': ['CG', 'CD1', 'CD2', 'CE1', 'CE2', 'CZ', 'HD1', 'HD2', 'HE1', 'HE2', 'HZ'],
    'TYR': ['CG', 'CD1', 'CD2', 'CE1', 'CE2', 'CZ', 'HD1', 'HD2', 'HE1', 'HE2', 'HH'],
    'TRP': ['CD2', 'CE2', 'CE3', 'CZ2', 'CZ3', 'CH2', 'HE3', 'HZ2', 'HZ3', 'HH2', 'HE1'],
    'HIS': ['CG', 'ND1', 'CD2', 'CE1', 'NE2', 'HD1', 'HD2', 'HE1', 'HE2', 'xx', 'yy']  
}

We also extract the number of unique chains(entity) and the number of copies of the chain(assembly) from the NMR-STAR file. There are two kid of sequence numbering available in both BMRB and PDB. One is author provided and other one is BMRB/PDB annotated. We have the option to chose which sequence number we want to extract from the file. This is crucial in the later stage while we combining data from BMRB and PDB.

The following function will create chemical shift dictionary from the star file

In [13]:

def get_chemical_shifts(str_file: str,auth_tag: Optional[bool] =False) -> tuple:
    """
    Extract the chemical shift information from  the NMR-STAR file
    :param str_file: NMR-STAR file name with full path
    :param auth_tag: use sequence id from Auth_seq_ID, optional
    :return: tuple of amide chemical  shift as dictionary, aromatic chemical shift as dictionary, entity size
        and entity and entity assembly size
    """
    str_data = pynmrstar.Entry.from_file(str_file)
    csdata = str_data.get_loops_by_category('Atom_chem_shift')
    entity = str_data.get_tag('_Entity_assembly.Entity_ID')
    entity_size = len(set(entity))
    assembly_size = (len(entity))
    amide_cs = {}
    aromatic_cs = {}
    for cs in csdata:
        tag_list = cs.get_tag_names()

        id2 = tag_list.index('_Atom_chem_shift.Auth_asym_ID')
        if auth_tag:
            id1 = tag_list.index('_Atom_chem_shift.Auth_seq_ID')
        else:
            id1 = tag_list.index('_Atom_chem_shift.Comp_index_ID')
        id3 = tag_list.index('_Atom_chem_shift.Comp_ID')
        id4 = tag_list.index('_Atom_chem_shift.Atom_ID')
        id5 = tag_list.index('_Atom_chem_shift.Val')
        id6 = tag_list.index('_Atom_chem_shift.Ambiguity_code')
        for d in cs.data:
            if d[id4] == 'H':
                if d[id2] == '.':
                    d[id2] = 'A'  # temp fix if asym id is missing
                amide_cs[(d[id1], d[id2], d[id3], d[id4])] = (d[id5], get_z_score(d[id3], float(d[id5])))
            if d[id3] in aromatic_atoms.keys():
                if d[id2] == '.':
                    d[id2] = 'A'  # temp fix if asym id is missing
                k = (d[id1], d[id2], d[id3])
                if d[id4] in aromatic_atoms[d[id3]]:
                    if k not in aromatic_cs.keys():
                        aromatic_cs[k] = {}
                    aromatic_cs[k][d[id4]] = (d[id5], d[id6])
    return amide_cs, aromatic_cs, entity_size, assembly_size

There are two ways one can get the required NMR-STAR file, either by directly downloading the file from BMRB or by using reboxitory in NMRBox. 

In [14]:
def get_bmrb_data(bmrb_id: Union[str,int],auth_tag: Optional[bool] = False, nmrbox: Optional[bool] =False):
    """
    Extract the chemical shift data for a given BMRB ID
    :param bmrb_id: BMRB ID
    :param auth_tag: Use sequence information from Auth_seq_ID, Optional
    :param nmrbox: Instead of BMRB-APR, use the NMR-STAR file from NMRBOx reboxitory. Optional
    :return: tuple of amide chemical  shift as dictionary, aromatic chemical shift as dictionary, entity size
        and entity and entity assembly size
    """
    if nmrbox:
        str_file_path = '/reboxitory/2021/07/BMRB/macromolecules/bmr{}/bmr{}_3.str'.format(
            bmrb_id,bmrb_id
        )
        bmrb_data = get_chemical_shifts(str_file_path, auth_tag)
    else:
        if not os.path.isdir('./data'):
            os.system('mkdir ./data')
        if not os.path.isdir('./data/BMRB'):
            os.system('mkdir ./data/BMRB')
        str_file = './data/BMRB/{}.str'.format(bmrb_id)
        if not os.path.isfile(str_file):
            cmd = 'wget http://rest.bmrb.io/bmrb/{}/nmr-star3 -O ./data/BMRB/{}.str'.format(bmrb_id, bmrb_id)
            os.system(cmd)
        bmrb_data = get_chemical_shifts('./data/BMRB/{}.str'.format(bmrb_id),auth_tag)
    return bmrb_data

For example let us fetch the chemical shift information for the BMRB entry  11086

In [15]:
bmrb_data = get_bmrb_data('11086')

In [16]:
amide_cs,aromatic_cs,entity_size,assembly_size = bmrb_data

Now we have all the required information in a dictionary format

In [17]:
amide_cs

{('5', 'A', 'SER', 'H'): ('7.774', -0.886),
 ('7', 'A', 'GLY', 'H'): ('8.328', -0.003),
 ('8', 'A', 'MET', 'H'): ('7.773', -0.831),
 ('9', 'A', 'ALA', 'H'): ('8.179', -0.026),
 ('10', 'A', 'VAL', 'H'): ('9.363', 1.659),
 ('11', 'A', 'ASN', 'H'): ('8.357', 0.054),
 ('12', 'A', 'VAL', 'H'): ('8.704', 0.659),
 ('13', 'A', 'TYR', 'H'): ('8.647', 0.497),
 ('14', 'A', 'SER', 'H'): ('8.089', -0.331),
 ('16', 'A', 'SER', 'H'): ('8.363', 0.151),
 ('17', 'A', 'VAL', 'H'): ('8.087', -0.278),
 ('18', 'A', 'THR', 'H'): ('8.142', -0.148),
 ('19', 'A', 'SER', 'H'): ('8.127', -0.264),
 ('20', 'A', 'GLU', 'H'): ('8.184', -0.253),
 ('21', 'A', 'ASN', 'H'): ('8.227', -0.159),
 ('22', 'A', 'LEU', 'H'): ('8.108', -0.171),
 ('23', 'A', 'SER', 'H'): ('9.170', 1.572),
 ('24', 'A', 'ARG', 'H'): ('9.176', 1.567),
 ('25', 'A', 'HIS', 'H'): ('7.841', -0.61),
 ('26', 'A', 'ASP', 'H'): ('7.880', -0.753),
 ('27', 'A', 'MET', 'H'): ('8.745', 0.859),
 ('28', 'A', 'LEU', 'H'): ('7.991', -0.357),
 ('29', 'A', 'ALA', 'H'

In [18]:
aromatic_cs

{('13', 'A', 'TYR'): {'HD1': ('7.024', '1'),
  'HD2': ('7.024', '1'),
  'HE1': ('6.703', '1'),
  'HE2': ('6.703', '1'),
  'CD1': ('131.006', '1'),
  'CD2': ('131.006', '1'),
  'CE1': ('115.768', '1'),
  'CE2': ('115.768', '1')},
 ('25', 'A', 'HIS'): {'HD2': ('7.050', '1'),
  'HE1': ('7.802', '1'),
  'CD2': ('117.899', '1'),
  'CE1': ('136.388', '1')},
 ('30', 'A', 'TRP'): {'HE1': ('8.707', '1'),
  'HE3': ('7.463', '1'),
  'HH2': ('5.666', '1'),
  'HZ2': ('4.899', '1'),
  'HZ3': ('6.503', '1'),
  'CE3': ('118.418', '1'),
  'CH2': ('120.768', '1'),
  'CZ2': ('112.300', '1'),
  'CZ3': ('118.671', '1')},
 ('36', 'A', 'HIS'): {'HD2': ('6.840', '1'),
  'HE1': ('8.128', '1'),
  'CD2': ('117.122', '1'),
  'CE1': ('134.589', '1')},
 ('39', 'A', 'TYR'): {'HD1': ('6.723', '1'),
  'HD2': ('6.723', '1'),
  'HE1': ('6.458', '1'),
  'HE2': ('6.458', '1'),
  'CD1': ('128.386', '1'),
  'CD2': ('128.386', '1'),
  'CE1': ('115.374', '1'),
  'CE2': ('115.374', '1')},
 ('51', 'A', 'TYR'): {'HD1': ('6.146',

In [19]:
entity_size

1

In [20]:
assembly_size

1

## Extract coordinate data from CIF file
We use mmcif library to parse the CIF file. The following function will parse the CIF file and extract the coordinate information as a dictionary

In [35]:

def get_coordinates(cif_file: str, auth_tag: Optional[bool] =True, nmrbox: Optional[bool] =False) -> dict:
    """
    Extract coordinate information from cif file as a dictionary
    {model_id : {(seq_id,chain_id,res_id,atom_id) : array[x,y,x],...},...}
    :param cif_file: Input CIF file with full path
    :param use_auth_tag: use sequence id from author provided tag
    :param nmrbox: use the gzip CIF file from NMRBox reboxitory
    :return: dictionary
    """
    cif_data = []
    if nmrbox:
        ifh = gzip.open(cif_file,'rt') # For NMRBox
    else:
        ifh = open(cif_file, 'r')
    pRd = PdbxReader(ifh)
    pRd.read(cif_data)
    ifh.close()
    c0 = cif_data[0]
    atom_site = c0.getObj('atom_site')
    max_models = int(atom_site.getValue('pdbx_PDB_model_num', -1))
    col_names = atom_site.getAttributeList()
    model_id = col_names.index('pdbx_PDB_model_num')
    x_id = col_names.index('Cartn_x')
    y_id = col_names.index('Cartn_y')
    z_id = col_names.index('Cartn_z')
    atom_id = col_names.index('label_atom_id')
    comp_id = col_names.index('label_comp_id')
    asym_id = col_names.index('label_asym_id')
    entity_id = col_names.index('label_entity_id')
    seq_id = col_names.index('label_seq_id')
    icode_id = col_names.index('pdbx_PDB_ins_code')
    alt_id = col_names.index('label_alt_id')
    aut_seq_id = col_names.index('auth_seq_id')
    aut_asym_id = col_names.index('auth_asym_id')
    aut_atom_id = col_names.index('auth_atom_id')
    aut_comp_id = col_names.index('auth_comp_id')
    pdb_models = {}
    atom_ids = {}
    for model in range(1, max_models + 1):
        pdb = {}
        aid = {}
        for dat in atom_site.getRowList():
            if dat[atom_id] == 'H' or dat[comp_id] in aromatic_atoms.keys():  # Only necessary coordinates for this
                # calculation
                if int(dat[model_id]) == model:
                    if auth_tag:
                        aid[(dat[aut_seq_id], dat[aut_asym_id], dat[aut_comp_id], dat[aut_atom_id])] = \
                            (dat[entity_id], dat[asym_id], dat[comp_id], dat[seq_id], dat[aut_seq_id],
                             dat[alt_id], dat[icode_id], dat[aut_asym_id])
                        pdb[(dat[aut_seq_id], dat[aut_asym_id], dat[aut_comp_id], dat[aut_atom_id])] = \
                            numpy.array([float(dat[x_id]), float(dat[y_id]), float(dat[z_id])])
                    else:
                        aid[(dat[seq_id], dat[asym_id], dat[comp_id], dat[atom_id])] = \
                            (dat[entity_id], dat[asym_id], dat[comp_id], dat[seq_id], dat[aut_seq_id],
                             dat[alt_id], dat[icode_id], dat[aut_asym_id])
                        pdb[(dat[seq_id], dat[asym_id], dat[comp_id], dat[atom_id])] = \
                            numpy.array([float(dat[x_id]), float(dat[y_id]), float(dat[z_id])])
        pdb_models[model] = pdb
        atom_ids[model] = aid
    return pdb_models


As before, we can either fetch the CIF file from wwPDB FTP archive or use the reboxitory in NMRBox

In [61]:

def get_pdb_data(pdb_id: str, auth_tag: Optional[bool] =False, nmrbox: Optional[bool]=False):
    """
    Extract coordinate data as dictionary for a given PDB ID
    :param pdb_id: PDB ID
    :param auth_tag: use sequence information from author tag
    :param nmrbox: Instead of download, use the gzip CIF file from NMRBox reboxitory
    :return: dictionary
    """
    if nmrbox:
        cif_file_path = '/reboxitory/2021/07/PDB/data/structures/all/mmCIF/{}.cif.gz'.format(pdb_id.lower())
        pdb_data = get_coordinates(cif_file_path,auth_tag,nmrbox=True)
    else:
        if not os.path.isdir('./data'):
            os.system('mkdir ./data')
        if not os.path.isdir('./data/PDB'):
            os.system('mkdir ./data/PDB')
        cif_file = './data/PDB/{}.cif'.format(pdb_id)
        if not os.path.isfile(cif_file):
            cmd = 'wget https://files.rcsb.org/download/{}.cif -O ./data/PDB/{}.cif'.format(pdb_id, pdb_id)
            os.system(cmd)
        pdb_data = get_coordinates('./data/PDB/{}.cif'.format(pdb_id),auth_tag)
    return pdb_data

For example let us extract the coordinate data for PDB 1WYO

In [62]:
pdb_data = get_pdb_data('1WYO')

Now we have coordinate data in a dictionary format  {model_id:{atom_identifier:array(x,y,z)}}

In [63]:
pdb_data

{1: {('2', 'A', 'SER', 'H'): array([19.53 , 26.151, -4.348]),
  ('3', 'A', 'SER', 'H'): array([17.618, 25.532, -6.564]),
  ('4', 'A', 'GLY', 'H'): array([14.666, 22.158, -7.628]),
  ('5', 'A', 'SER', 'H'): array([16.051, 18.1  , -6.147]),
  ('6', 'A', 'SER', 'H'): array([13.223, 18.264, -6.514]),
  ('7', 'A', 'GLY', 'H'): array([11.363, 16.116, -6.81 ]),
  ('8', 'A', 'MET', 'H'): array([10.451, 14.874, -3.233]),
  ('9', 'A', 'ALA', 'H'): array([12.416, 11.478, -1.109]),
  ('10', 'A', 'VAL', 'H'): array([ 9.497, 12.293,  2.112]),
  ('11', 'A', 'ASN', 'H'): array([12.883, 11.578,  4.345]),
  ('12', 'A', 'VAL', 'H'): array([11.646,  8.483,  7.579]),
  ('13', 'A', 'TYR', 'N'): array([11.422,  9.952, 11.315]),
  ('13', 'A', 'TYR', 'CA'): array([12.201,  9.721, 12.525]),
  ('13', 'A', 'TYR', 'C'): array([11.299,  9.296, 13.68 ]),
  ('13', 'A', 'TYR', 'O'): array([11.31 ,  8.139, 14.099]),
  ('13', 'A', 'TYR', 'CB'): array([12.977, 10.982, 12.907]),
  ('13', 'A', 'TYR', 'CG'): array([14.235, 

## Calculate the distance, azimuthal angle and solid angle

Before we begin, let us define some useful functions
### Distance between two points in space

In [64]:

def get_distance(c1 : numpy.ndarray ,c2 : numpy.ndarray) -> numpy.ndarray:
    """
    Calculates the distance between two coordinate points
    :param c1: array of x,y,z
    :param c2: array of x,y,z
    :return: distance between two ponts
    """
    return numpy.linalg.norm(c1 - c2)


### Centroid of given set of points in a plane

In [65]:
def get_centroid(p:List[numpy.ndarray]) -> numpy.ndarray:
    """
    Calculate the center of given sent of points
    :param p list of arrray of x,y,z: 
    :return array of x,yx,z: 
    """
    # print (len(p),p)
    x = [i[0] for i in p]
    y = [i[1] for i in p]
    z = [i[2] for i in p]
    c = [sum(x) / len(p), sum(y) / len(p), sum(z) / len(p)]
    return numpy.array(c)

### Solid angle for a given azimuthal angle at the distance

In [66]:
def solid_angle(a_deg : float, r: float) -> float:
    """
    Calculate the solid angle from the azimuthal angle and the disance
    :param a_deg: Azimuthal angle
    :param r: Distance from amide proton to the center of the ring
    :return: solid angle
    """
    s = 1.4 #C-C bond length
    A=((3.0*numpy.sqrt(3))/2.0)*s*s #area of the hexagonal plane
    a = (numpy.pi / 180) * a_deg
    # sa2=2*numpy.pi*(1.0-1.0/(numpy.sqrt(1+(A*numpy.cos(a)/(numpy.pi*r1**r1)))))
    sa = 2 * numpy.pi * (1.0 - 1.0 / (numpy.sqrt(1 + (A*numpy.cos(a) / (numpy.pi * r * r)))))
    # print (a_deg)
    sa_deg = (180.0 / numpy.pi) * sa
    # sa_deg2 = (180.0 / numpy.pi) * sa2
    # print (a_deg,sa_deg,sa_deg2)
    return sa_deg

### Azimithal anlge and solid angle 

In [67]:

def find_angle(ring_info: tuple, amide_position: numpy.ndarray, d: float)-> tuple:
    """
    Calculate the azimuthal angle 
    :param ring_info: touble (ring center, list of position of ring atoms
    :param amide_position: position of amide proton
    :param d: distanace
    :return: azimuthal angle, solid angle
    """
    pc, ring_info = ring_info
    v1 = ring_info[1] - pc
    v2 = ring_info[2] - pc
    nv = numpy.cross(v1, v2)
    #nv2 = numpy.cross(v2, v1)
    cv = amide_position - pc
    #cv2 = c - cn
    nnv = nv / numpy.linalg.norm(nv)
    ncv = cv / numpy.linalg.norm(cv)
    #ncv2 = cv2 / numpy.linalg.norm(cv2)
    dp = abs(numpy.dot(nnv, ncv))
    #dp2 = abs(numpy.dot(nnv, ncv2))
    ang = numpy.arccos(dp)
    #ang2 = numpy.arccos(dp2)
    ang_deg = (180 / numpy.pi) * ang
    #ang_deg2 = (180 / numpy.pi) * ang2
    # print(ang_deg)
    s_ang = solid_angle(ang_deg, d)
    return ang_deg, s_ang


The following function extracts geometric information about aromatic residues from the pdb data

In [68]:
def get_aromatic_info(pdb_data: dict) -> dict:
    """
    Extract the necessary aromatic residue information from the pdb data
    :param pdb_data: pdb data oject from get_pdb_data
    :return: dictionary
    """
    aromatic_atoms = {
        'PHE': ['CG', 'CD1', 'CD2', 'CE1', 'CE2', 'CZ', 'HD1', 'HD2', 'HE1', 'HE2', 'HZ'],
        'TYR': ['CG', 'CD1', 'CD2', 'CE1', 'CE2', 'CZ', 'HD1', 'HD2', 'HE1', 'HE2', 'HH'],
        'TRP': ['CD2', 'CE2', 'CE3', 'CZ2', 'CZ3', 'CH2', 'HE3', 'HZ2', 'HZ3', 'HH2', 'HE1'],
        'HIS': ['CG', 'ND1', 'CD2', 'CE1', 'NE2', 'HD1', 'HD2', 'HE1', 'HE2', 'xx', 'yy']  # if needed un comment
    }
    ring_atoms = {
        'PHE': ['CG', 'CD1', 'CD2', 'CE1', 'CE2', 'CZ'],
        'TYR': ['CG', 'CD1', 'CD2', 'CE1', 'CE2', 'CZ'],
        'TRP': ['CD2', 'CE2', 'CE3', 'CZ2', 'CZ3', 'CH2'],
        'HIS': ['CG', 'ND1', 'CD2', 'CE1', 'NE2', ]  # if needed un comment
    }
    aromtic_residues = sorted(
        list(set([(int(i[0]), i[1], i[2]) for i in pdb_data[1].keys() if i[2] in aromatic_atoms.keys()])))
    ar_info = {}
    for m in pdb_data.keys():
        ar_info[m] = {}
        for ar_res in aromtic_residues:
            p = []
            for atm in ring_atoms[ar_res[2]]:
                p.append(pdb_data[m][(str(ar_res[0]), ar_res[1], ar_res[2], atm)])
            c = get_centroid(p)
            ar_info[m][(str(ar_res[0]), ar_res[1], ar_res[2])] = (c, p)
    return ar_info


In [69]:
ar_info = get_aromatic_info(pdb_data)

In [70]:
ar_info

{1: {('13', 'A', 'TYR'): (array([15.40066667, 11.37766667, 11.3405    ]),
   [array([14.235, 11.188, 12.094]),
    array([14.266, 10.89 , 10.737]),
    array([15.394, 11.679, 12.682]),
    array([15.413, 11.075,  9.99 ]),
    array([16.546, 11.869, 11.943]),
    array([16.55 , 11.565, 10.597])]),
  ('25', 'A', 'HIS'): (array([-11.8754,  -1.885 ,  12.2712]),
   [array([-10.79 ,  -2.174,  12.592]),
    array([-11.67 ,  -1.329,  13.236]),
    array([-11.437,  -2.617,  11.489]),
    array([-12.798,  -1.266,  12.552]),
    array([-12.682,  -2.039,  11.487])]),
  ('30', 'A', 'TRP'): (array([-1.3265    ,  4.15916667,  5.44733333]),
   [array([-2.59 ,  4.198,  6.054]),
    array([-2.028,  5.334,  5.439]),
    array([-1.862,  3.005,  6.056]),
    array([-0.775,  5.309,  4.832]),
    array([-0.619,  2.982,  5.454]),
    array([-0.085,  4.127,  4.849])]),
  ('36', 'A', 'HIS'): (array([-12.7942,   5.2816,  -2.33  ]),
   [array([-12.005,   4.456,  -2.574]),
    array([-13.324,   4.288,  -2.208]),
 

The following function analyzes the NMR ensemble and calculates the mean, median, standard deviation, min and miximum of distance, azimithal angle and solid angle of the nearest aromatic ring. 

In [71]:
def analyze_enzemble(ar_info: dict,pdb_data: dict) -> tuple:
    """
    Calculates the distance, azimuthal angle and solid angle for all amide-aromatic pair in the enzemble
    :param ar_info: aromatic residue information as dictionary
    :param pdb_data: pdb data as dictionary
    :return: tuple (distance, angle , solid angle)
    """
    amide_res = {}
    for m in pdb_data.keys():
        amide_res[m]={}
        for atm in pdb_data[m].keys():
            if atm[3]=='H':
                amide_res[m][atm]=pdb_data[m][atm]
    dist={}
    angle={}
    solid_angle={}
    for atm in amide_res[1].keys():
        dist[atm]={}
        angle[atm]={}
        solid_angle[atm]={}
        for ar_res in ar_info[1].keys():
            d=[]
            a=[]
            sa=[]
            for m in amide_res.keys():
                d1=get_distance(ar_info[m][ar_res][0],amide_res[m][atm])
                d.append(d1)
                ang = find_angle(ar_info[m][ar_res],amide_res[m][atm],d1)
                a.append(ang[0])
                sa.append(ang[1])
            dist[atm][ar_res]=[round(numpy.mean(d),3),round(numpy.median(d),3),round(numpy.std(d),3),round(min(d),3),round(max(d),3)]
            angle[atm][ar_res]=[round(numpy.mean(a),3),round(numpy.median(a),3),round(numpy.std(a),3),round(min(a),3),round(max(a),3)]
            solid_angle[atm][ar_res]=[round(numpy.mean(sa),3),round(numpy.median(sa),3),round(numpy.std(sa),3),round(min(sa),3),round(max(sa),3)]
    s_dist={}
    for aa in dist.keys():
        sorted_dist = sorted(dist[aa].items(), key=lambda kv: kv[1][0])
        s_dist[aa]=sorted_dist
    return s_dist,angle,solid_angle


In [72]:
sorted_dist,azi_angle,sold_angle=analyze_enzemble(ar_info,pdb_data)

All the data in dictionary format and we try to maintain the same key throuout the analysis

In [73]:
sorted_dist

{('2',
  'A',
  'SER',
  'H'): [(('59', 'A', 'PHE'),
   [17.376, 17.42, 2.53, 12.84, 22.491]), (('13', 'A', 'TYR'), [19.889,
    18.759,
    4.299,
    14.071,
    30.569]), (('121', 'A', 'PHE'),
   [20.177, 20.58, 2.961, 13.844, 25.288]), (('126', 'A', 'TYR'), [21.601,
    22.774,
    5.13,
    5.614,
    28.85]), (('89', 'A', 'PHE'),
   [22.843, 22.946, 3.022, 15.074, 27.219]), (('122', 'A', 'PHE'), [23.081,
    23.847,
    4.603,
    9.362,
    30.333]), (('117', 'A', 'TRP'),
   [23.583, 23.932, 3.156, 16.749, 29.729]), (('118', 'A', 'PHE'), [25.08,
    25.18,
    3.493,
    16.469,
    31.433]), (('131', 'A', 'TYR'),
   [25.225, 25.189, 3.583, 15.947, 32.307]), (('54', 'A', 'PHE'), [26.574,
    26.943,
    3.854,
    15.443,
    33.692]), (('30', 'A', 'TRP'),
   [27.178, 27.755, 4.458, 13.971, 33.969]), (('64', 'A', 'HIS'), [27.55,
    28.841,
    5.238,
    13.367,
    34.317]), (('114', 'A', 'PHE'),
   [28.243, 28.363, 3.217, 21.665, 33.228]), (('51', 'A', 'TYR'), [29.416,
    29

In [74]:
azi_angle

{('2',
  'A',
  'SER',
  'H'): {('13', 'A', 'TYR'): [61.746, 59.954, 20.943, 10.062, 88.055], ('25',
   'A',
   'HIS'): [32.861, 28.068, 16.11, 12.709, 75.818], ('30',
   'A',
   'TRP'): [71.885, 70.854, 8.628, 52.175, 87.71], ('36', 'A', 'HIS'): [72.812,
   75.23,
   8.539,
   52.525,
   83.268], ('39', 'A', 'TYR'): [82.62, 83.833, 5.148, 72.3, 89.852], ('51',
   'A',
   'TYR'): [55.511, 53.113, 9.57, 42.302, 73.202], ('54', 'A', 'PHE'): [71.235,
   70.436,
   9.993,
   56.027,
   89.571], ('59', 'A', 'PHE'): [57.807, 55.241, 18.176, 32.211, 88.32], ('64',
   'A',
   'HIS'): [37.206, 35.558, 14.73, 7.109, 66.571], ('70', 'A', 'PHE'): [74.569,
   75.092,
   7.355,
   59.47,
   89.266], ('76', 'A', 'HIS'): [49.5, 48.18, 12.338, 21.637, 72.007], ('78',
   'A',
   'TYR'): [68.422, 66.462, 11.83, 48.538, 89.685], ('80',
   'A',
   'HIS'): [30.436, 28.683, 7.409, 17.902, 41.906], ('82',
   'A',
   'PHE'): [82.298, 83.227, 5.628, 71.428, 89.718], ('89',
   'A',
   'PHE'): [31.462, 26.631, 19

In [75]:
sold_angle

{('2',
  'A',
  'SER',
  'H'): {('13', 'A', 'TYR'): [0.376, 0.363, 0.287, 0.039, 0.957], ('25',
   'A',
   'HIS'): [0.163, 0.151, 0.085, 0.053, 0.493], ('30', 'A', 'TRP'): [0.149,
   0.131,
   0.124,
   0.011,
   0.566], ('36', 'A', 'HIS'): [0.093, 0.058, 0.098, 0.024, 0.481], ('39',
   'A',
   'TYR'): [0.031, 0.029, 0.025, 0.001, 0.092], ('51', 'A', 'TYR'): [0.192,
   0.187,
   0.054,
   0.081,
   0.354], ('54', 'A', 'PHE'): [0.145, 0.12, 0.103, 0.004, 0.41], ('59',
   'A',
   'PHE'): [0.556, 0.624, 0.386, 0.022, 1.488], ('64', 'A', 'HIS'): [0.357,
   0.284,
   0.264,
   0.132,
   1.314], ('70', 'A', 'PHE'): [0.076, 0.073, 0.04, 0.005, 0.169], ('76',
   'A',
   'HIS'): [0.113, 0.109, 0.032, 0.059, 0.194], ('78', 'A', 'TYR'): [0.068,
   0.067,
   0.042,
   0.002,
   0.187], ('80', 'A', 'HIS'): [0.234, 0.202, 0.112, 0.144, 0.677], ('82',
   'A',
   'PHE'): [0.043, 0.032, 0.036, 0.002, 0.131], ('89', 'A', 'PHE'): [0.456,
   0.452,
   0.156,
   0.183,
   0.936], ('108', 'A', 'PHE'): [0.17

## Combine the above steps and analyze the amide-aromatic interaction for a given pair of PDB and BMRB ids
This is the final step in which we combine the information from two different database using atom identifier. As mentioned before, both data dictionaries are having same set of keys. First we find out which sequence numbering matches between the two files. Then information from both databases combined using matching sequence and atom identifier (dictionary keys) 

In [76]:

def calculate_interaction(pdb: dict,bmrb: dict ,nmrbox: Optional[bool]=False)-> None:
    """
    Combines the geometric information form PDB and chemical shift Z-score from the BMRB and writes out CSV file
    :param pdb: pdb information as dictionary
    :param bmrb: bmrb information as dictinary
    :param nmrbox: use the NMRBox reboxitory
    """
    pdb_data_actual = get_pdb_data(pdb,auth_tag=False,nmrbox=nmrbox)
    bmrb_data_actual = get_bmrb_data(bmrb,auth_tag=False,nmrbox=nmrbox)
    pdb_data_auth = get_pdb_data(pdb,auth_tag=True,nmrbox=nmrbox)
    bmrb_data_auth = get_bmrb_data(bmrb,auth_tag=True,nmrbox=nmrbox)
    if pdb_data_actual is not None and pdb_data_auth is not None and bmrb_data_actual \
            is not None and bmrb_data_auth is not None:
        pdb_actual_keys = [i for i in pdb_data_actual[1].keys() if i[3] == 'H']
        pdb_auth_keys = [i for i in pdb_data_auth[1].keys() if i[3] == 'H']
        bmrb_actual_keys = [i for i in bmrb_data_actual[0].keys() if i[3]=='H']
        bmrb_auth_keys = [i for i in bmrb_data_auth[0].keys() if i[3] == 'H']
        actual_actual = [i for i in bmrb_actual_keys if i in pdb_actual_keys]
        actual_auth = [i for i in bmrb_actual_keys if i in pdb_auth_keys]
        auth_actual = [i for i in bmrb_auth_keys if i in pdb_actual_keys]
        auth_auth= [i for i in bmrb_auth_keys if i in pdb_auth_keys]
        if len(bmrb_actual_keys)>0:
            seq_len = float(len(bmrb_actual_keys))
            actual_actual_match = float(len(actual_actual))/seq_len
            actual_auth_match = float(len(actual_auth))/seq_len
            auth_actual_match = float(len(auth_actual))/seq_len
            auth_auth_match = float(len(auth_auth))/seq_len
            if actual_actual_match > 0.5:
                pdb_data = pdb_data_actual
                bmrb_data = bmrb_data_actual
                tag_match = 'ORIG_ORIG'
            elif actual_auth_match > 0.7:
                pdb_data = pdb_data_auth
                bmrb_data = bmrb_data_actual
                tag_match = 'ORIG_AUTH'
            elif auth_actual_match > 0.7:
                pdb_data = pdb_data_actual
                bmrb_data = bmrb_data_auth
                tag_match = 'AUTH_ORIG'
            elif auth_auth_match > 0.7:
                pdb_data = pdb_data_auth
                bmrb_data = bmrb_data_auth
                tag_match = 'AUTH_AUTH'
            else:
                tag_match = None
            if tag_match is not None:
                amide_chemical_shift, aromatic_chemical_shift, entity_size, assembly_size = bmrb_data
                ar_info = get_aromatic_info(pdb_data)
                dist,angle,solid_angle = analyze_enzemble(ar_info,pdb_data)
                if not os.path.isdir('./data'):
                    os.system('mkdir ./data')
                if not os.path.isdir('./data/output'):
                    os.system('mkdir ./data/output')
                fo_name = 'data/output/{}-{}-{}.csv'.format(pdb,bmrb,tag_match)
                fo=open(fo_name,'w')
                header = 'pdb_id,bmrb_id,entity_size,assembly_size,' \
                         'amide_seq_id,amide_chain_id,amide_res,amide_cs,amide_z,' \
                         'aro_seq_id,aro_chain_id,aro_res,' \
                         'mean_d,meidan_d,std_d,min_d,max_d,' \
                         'mena_ang,median_ang,std_and,min_ang,max_ang,' \
                         'mean_sang,median_sang,std_sang,min_sang,max_sang\n'
                fo.write(header)
                for atm in amide_chemical_shift.keys():
                    # print (atm,amide_chemical_shift[atm],dist[atm][0],angle[atm][dist[atm][0][0]],
                    #        solid_angle[atm][dist[atm][0][0]] )
                    try:
                        fo.write('{},{},{},{},{},{},{},{},{},{},{},{},{},{},{}\n'.format(pdb,bmrb,
                                                                                         entity_size,assembly_size,
                                                                                         atm[0],atm[1],atm[2],
                               amide_chemical_shift[atm][0],amide_chemical_shift[atm][1],
                               dist[atm][0][0][0],dist[atm][0][0][1],dist[atm][0][0][2],
                               ','.join([str(i) for i in dist[atm][0][1]]),
                               ','.join([str(i) for i in angle[atm][dist[atm][0][0]]]),
                               ','.join([str(i) for i in solid_angle[atm][dist[atm][0][0]]])))
                    except KeyError:
                        logging.warning('Missing key {}'.format(atm))
                    except IndexError:
                        logging.warning('No aromatic residue')
                fo.close()


### Example : Alalysis of 1WYO and 11086

In [78]:
calculate_interaction('1WYO','11086')

In [79]:
cat data/output/1WYO-11086-ORIG_ORIG.csv

pdb_id,bmrb_id,entity_size,assembly_size,amide_seq_id,amide_chain_id,amide_res,amide_cs,amide_z,aro_seq_id,aro_chain_id,aro_res,mean_d,meidan_d,std_d,min_d,max_d,mena_ang,median_ang,std_and,min_ang,max_ang,mean_sang,median_sang,std_sang,min_sang,max_sang
1WYO,11086,1,1,5,A,SER,7.774,-0.886,59,A,PHE,11.58,12.036,1.269,8.662,13.637,63.952,65.477,20.586,20.884,89.982,0.85,0.816,0.63,0.001,2.376
1WYO,11086,1,1,7,A,GLY,8.328,-0.003,59,A,PHE,6.504,6.977,1.342,4.296,8.341,67.543,67.766,12.401,47.783,88.678,2.528,2.785,1.086,0.121,4.113
1WYO,11086,1,1,8,A,MET,7.773,-0.831,59,A,PHE,5.425,5.452,0.586,3.928,6.584,55.538,54.443,11.175,40.328,84.259,5.633,5.337,2.382,0.897,12.696
1WYO,11086,1,1,9,A,ALA,8.179,-0.026,59,A,PHE,5.625,5.644,0.247,4.868,5.996,29.049,27.633,6.193,20.493,46.837,7.807,7.847,0.98,6.253,10.904
1WYO,11086,1,1,10,A,VAL,9.363,1.659,121,A,PHE,4.773,4.68,0.577,3.709,6.099,66.462,68.098,8.953,47.856,81.125,4.989,4.947,1.771,2.115,9.933
1WYO,11086,1,1,11,A,ASN,8.357,0.054,13,A,TYR,6

## Plotting the results
Here is some of the example plots from the csv file

In [80]:
def plot_d_vs_z(csv_file):
    with open(csv_file, "r") as csvfile:
        csvreader = csv.reader(csvfile)
        next(csvreader, None)
        z=[]
        d=[]
        ang=[]
        sang=[]
        lab=[]
        ar_res=[]
        for row in csvreader:
            info = '{}-{}-{}-{}-{}-{}/{}/{}/{}'.format(row[0],row[1],row[5],row[6],row[9],row[11],row[7],row[8],row[12])
            d.append(float(row[12]))
            z.append(float(row[8]))
            ang.append(float(row[17]))
            sang.append(float(row[22]))
            ar_res.append(row[11])
            lab.append(info)
    fig = px.scatter(x=d,y=z,color=ar_res,hover_name=lab,
                     labels=dict(x='Distance (Å)', y='Z-score'),)
    fig.show()

def plot_azimuthal_vs_z(csv_file):
    with open(csv_file, "r") as csvfile:
        csvreader = csv.reader(csvfile)
        next(csvreader, None)
        z = []
        d = []
        ang = []
        sang = []
        lab = []
        ar_res = []
        for row in csvreader:
            info = '{}-{}-{}-{}-{}-{}/{}/{}/{}'.format(row[0], row[1], row[5], row[6], row[9], row[11], row[7],
                                                       row[8], row[12])
            d.append(float(row[12]))
            z.append(float(row[8]))
            ang.append(float(row[17]))
            sang.append(float(row[22]))
            ar_res.append(row[11])
            lab.append(info)
    fig = px.scatter(x=ang, y=z, color=ar_res, hover_name=lab,
                     labels=dict(x='Azimuthal angle', y='Z-score'), )
    fig.show()

def plot_solidangle_vs_z(csv_file):
    with open(csv_file, "r") as csvfile:
        csvreader = csv.reader(csvfile)
        next(csvreader, None)
        z = []
        d = []
        ang = []
        sang = []
        lab = []
        ar_res = []
        for row in csvreader:
            info = '{}-{}-{}-{}-{}-{}/{}/{}/{}'.format(row[0], row[1], row[5], row[6], row[9], row[11], row[7],
                                                       row[8], row[12])
            d.append(float(row[12]))
            z.append(float(row[8]))
            ang.append(float(row[17]))
            sang.append(float(row[22]))
            ar_res.append(row[11])
            lab.append(info)
    fig = px.scatter(x=sang, y=z, color=ar_res, hover_name=lab,
                     labels=dict(x='Solid angle', y='Z-score'), )
    fig.show()
def plot_d_vs_solidangle(csv_file):
    with open(csv_file, "r") as csvfile:
        csvreader = csv.reader(csvfile)
        next(csvreader, None)
        z=[]
        d=[]
        ang=[]
        sang=[]
        lab=[]
        ar_res=[]
        for row in csvreader:
            info = '{}-{}-{}-{}-{}-{}/{}/{}/{}'.format(row[0],row[1],row[5],row[6],row[9],row[11],row[7],row[8],row[12])
            d.append(float(row[12]))
            z.append(float(row[8]))
            ang.append(float(row[17]))
            sang.append(float(row[22]))
            ar_res.append(row[11])
            lab.append(info)
    fig = px.scatter(x=d,y=sang,color=ar_res,hover_name=lab,
                     labels=dict(x='Distance (Å)', y='Solid angle'),)
    fig.show()

def plot_3d(csv_file):
    with open(csv_file, "r") as csvfile:
        csvreader = csv.reader(csvfile)
        next(csvreader, None)
        z = []
        d = []
        ang = []
        sang = []
        lab = []
        ar_res = []
        for row in csvreader:
            info = '{}-{}-{}-{}-{}-{}/{}/{}/{}'.format(row[0], row[1], row[5], row[6], row[9], row[11], row[7],
                                                       row[8], row[12])
            d.append(float(row[12]))
            z.append(float(row[8]))
            ang.append(float(row[17]))
            sang.append(float(row[22]))
            ar_res.append(row[11])
            lab.append(info)
    fig = px.scatter_3d(x=d, y=ang, z=z, color=ar_res, hover_name=lab,
                     labels=dict(x='Distance (Å)', z='Z-score', y='Azimuthal angle'), )
    fig.show()


In [81]:
plot_d_vs_solidangle('data/output/1WYO-11086-ORIG_ORIG.csv')

In [34]:
plot_d_vs_z('data/output/1WYO-11086-ORIG_ORIG.csv')

In [35]:
plot_azimuthal_vs_z('data/output/1WYO-11086-ORIG_ORIG.csv')

In [36]:
plot_solidangle_vs_z('data/output/1WYO-11086-ORIG_ORIG.csv')

In [37]:
plot_3d('data/output/1WYO-11086-ORIG_ORIG.csv')

## Database wide analysis
We can generate the data for all matching PDB and BMRB entires and concatenate all the csv files. The above plotting functions can be used to analyze the concatenated csv file. 